In [1]:
import pandas as pd
import re
import math
import torch
from torch import nn
from torch.utils.data import Dataset, DataLoader
import matplotlib.pyplot as plt
from torch.nn.utils.rnn import pad_sequence

In [2]:
if torch.cuda.is_available():
    print("CUDA is available!")
    print(f"CUDA device count: {torch.cuda.device_count()}")
    print(f"Current CUDA device name: {torch.cuda.get_device_name(0)}")
else:
    print("CUDA is not available. PyTorch will use the CPU.")

CUDA is available!
CUDA device count: 1
Current CUDA device name: NVIDIA GeForce RTX 4080 SUPER


In [3]:
import sentencepiece as spm

from tqdm import tqdm
import random

file = "amazon_review.csv"

data = pd.read_csv(file).dropna(ignore_index=True)

data["reviewText"].to_csv("amazon_reviews.txt", index=False, header=False)
data["overall"] = data["overall"] -1

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

vocab_size = 16000
start_token = 16000
end_token = 16001

'''
spm.SentencePieceTrainer.train(
    input='amazon_reviews.txt',
    model_prefix='amazon_reviews',
    vocab_size=vocab_size,
    model_type='unigram',
    character_coverage=1.0
)
'''

tok = spm.SentencePieceProcessor(model_file='amazon_reviews.model')

print(tok.encode("This book is amazing!", out_type=int))

ls  = [len(tok.encode(i, out_type=int)) for i in data["reviewText"]]

data["lengths"] = ls

data_trunc = data[data["lengths"]<=80]

v = data_trunc["overall"].value_counts()

balanced_data = (
    data_trunc.groupby("overall")
      .sample(n=min(v), random_state=42)
      .reset_index(drop=True)
)

filter_ = 1


df_shuffled = balanced_data.sample(frac=filter_, random_state=42).reset_index(drop=True)

# Split the shuffled DataFrame
train_size = 0.8
train_df = df_shuffled.sample(frac=train_size, random_state=42).reset_index(drop=True)
test_df = df_shuffled.drop(train_df.index).reset_index(drop=True)

len_train = len(train_df)
len_test = len(test_df)

print("Train Size: ", len(train_df))
print("Test Size: ", len(test_df))

num_rows = 2000

n = [0, 1, 2, 3, 5, 7, 10]
def getEncoding(df, i):
    row_input = [16000] + tok.encode(df["reviewText"].iloc[i], out_type=int) + [16001]
    row_output = tok.encode(str(df["overall"].iloc[i]), out_type = int)
    return row_input, row_output

annos_x = {}
for i in n:
    annos_x[i]=[]
annos_y = []
for i in tqdm(range(num_rows)):
    k = random.randint(0,len(test_df) - 1)
    #input_fin = test_df["reviewText"][k]
    #output_fin = test_df["overall"][k]
    input_fin, output_fin = getEncoding(test_df, i)
    icl_df = test_df.drop(test_df.index[k])
    for j in n:
        s= icl_df.sample(n=j)
        in_ = []
        for shot in range(j):
            inp, outp = getEncoding(s, shot)
            in_.extend(inp)
            in_.extend(outp)
            
            print("in: ", inp)
            print(str(s["overall"].iloc[shot]))
            print("out: ", outp)
        in_.extend(input_fin)
        annos_x[j].append(in_)
    annos_y.extend(output_fin)





[109, 2071, 13, 828, 34]
Train Size:  15396
Test Size:  3849


  2%|▊                                       | 42/2000 [00:00<00:04, 419.82it/s]

in:  [16000, 266, 5, 5033, 75, 6, 23, 5, 397, 369, 57, 11, 25, 3, 1498, 364, 24, 9, 110, 2690, 25, 4, 264, 9, 86, 82, 11, 23, 790, 4, 69, 46, 1794, 11, 8, 103, 73, 7, 18, 141, 256, 5393, 65, 5, 1359, 727, 16001]
out:  [259, 3, 2517]
in:  [16000, 336, 38, 6, 22, 113, 603, 8, 120, 37, 2512, 3, 139, 49, 7, 8, 120, 1091, 25, 55, 136, 930, 494, 148, 3, 1145, 8, 229, 17, 24, 16, 225, 240, 7, 22, 19, 241, 121, 60, 42, 10, 221, 170, 3, 16001]
out:  [303, 3, 2517]
in:  [16000, 1803, 425, 56, 98, 50, 4, 27, 149, 19, 5, 161, 30, 3, 16001]
out:  [468, 3, 2517]
in:  [16000, 255, 148, 6, 55, 53, 117, 124, 16001]
out:  [468, 3, 2517]
in:  [16000, 4397, 46, 1637, 7291, 157, 126, 3, 1598, 10, 29, 27, 200, 1430, 71, 5, 73, 6, 37, 826, 11762, 14, 71, 873, 3, 3655, 665, 1766, 7286, 5, 98, 75, 33, 874, 5, 161, 3, 1511, 15, 65, 2445, 97, 24, 19, 2375, 3, 16001]
out:  [3210, 3, 2517]
in:  [16000, 38, 26, 274, 40, 6, 40, 49, 16001]
out:  [259, 3, 2517]
in:  [16000, 4, 318, 8, 381, 3, 2424, 10, 29, 145, 353, 6

  4%|█▋                                      | 86/2000 [00:00<00:04, 418.56it/s]

in:  [16000, 616, 10, 29, 2427, 34, 16001]
out:  [186, 3, 2517]
in:  [16000, 483, 61, 16001]
out:  [303, 3, 2517]
in:  [16000, 70, 13, 51, 106, 3, 478, 33, 53, 121, 271, 684, 5, 1674, 11, 65, 37, 4, 64, 9, 737, 14, 143, 16001]
out:  [259, 3, 2517]
in:  [16000, 4, 398, 5, 4907, 30, 3, 1057, 437, 186, 276, 53, 117, 3, 16001]
out:  [468, 3, 2517]
in:  [16000, 39, 30, 330, 7152, 7, 22, 1410, 10, 29, 145, 633, 3, 710, 438, 67, 380, 282, 17, 153, 276, 7152, 7, 22, 26, 38, 3, 39, 280, 1868, 4, 10, 76, 743, 3, 45, 284, 7152, 23, 66, 43, 3157, 67, 7152, 10, 16001]
out:  [3210, 3, 2517]
in:  [16000, 4, 660, 10, 29, 179, 21, 406, 6, 23, 22, 19, 87, 11, 5, 12, 2880, 2975, 5316, 8360, 84, 4, 58, 46, 9856, 681, 3, 16001]
out:  [303, 3, 2517]
in:  [16000, 269, 7, 38, 168, 16001]
out:  [303, 3, 2517]
in:  [16000, 45, 86, 82, 23, 19, 2070, 16001]
out:  [468, 3, 2517]
in:  [16000, 4, 10, 108, 299, 206, 35, 59, 50, 11, 1956, 101, 3, 4, 43, 21, 176, 56, 749, 10, 15, 11, 59, 7, 22, 10, 131, 114, 7377, 5, 6

...

in:  [16000, 9200, 159, 184, 1065, 5, 297, 17, 18, 1101, 10, 15, 254, 3, 175, 99, 8, 432, 711, 254, 3, 175, 286, 8, 432, 447, 75, 3, 45, 436, 43, 82, 211, 3, 95, 1101, 33, 429, 24, 216, 10, 29, 26, 3, 181, 697, 230, 6, 228, 248, 7, 116, 750, 3, 16001]
out:  [468, 3, 2517]
in:  [16000, 4, 81, 21, 35, 8, 589, 323, 3, 16001]
out:  [186, 3, 2517]
in:  [16000, 206, 19, 61, 208, 686, 807, 65, 8815, 42, 6, 5, 50, 19, 55, 8, 74, 205, 56, 105, 3, 188, 74, 66, 650, 173, 5, 355, 56, 4, 43, 23, 3056, 4, 58, 36, 5307, 21, 3, 16001]
out:  [259, 3, 2517]
in:  [16000, 2761, 119, 9, 91, 200, 54, 16001]
out:  [303, 3, 2517]
in:  [16000, 4, 107, 532, 429, 16, 31, 130, 3, 4, 81, 24, 44, 11, 18, 142, 35, 8, 323, 79, 3, 175, 299, 21, 114, 259, 348, 7, 28, 5, 154, 62, 5, 44, 1023, 894, 174, 906, 3, 39, 75, 13, 4216, 178, 3, 175, 172, 1600, 5, 2035, 520, 17, 202, 75, 9, 998, 14, 7, 894, 8, 793, 17, 3, 266, 8, 195, 1175, 16001]
out:  [3210, 3, 2517]
in:  [16000, 806, 9, 41, 6, 291, 311, 6, 55, 43, 90, 42, 337,

 96%|████████████████████████████████████▋ | 1928/2000 [00:04<00:00, 424.63it/s]

in:  [16000, 1076, 26, 35, 105, 7, 138, 319, 40, 1860, 3, 95, 182, 13, 40, 195, 32, 202, 50, 3, 16001]
out:  [259, 3, 2517]
in:  [16000, 96, 986, 26, 2237, 94, 192, 531, 4, 27, 287, 179, 3, 4, 207, 18, 640, 30, 6, 23, 5, 980, 542, 671, 3541, 980, 28, 18, 542, 7, 5, 986, 19, 675, 650, 71, 5, 615, 846, 22, 26, 217, 28, 297, 3, 45, 63, 1131, 461, 23, 4, 170, 9, 160, 77, 226, 9, 248, 21, 3, 16001]
out:  [468, 3, 2517]
in:  [16000, 45, 86, 82, 23, 19, 2070, 16001]
out:  [468, 3, 2517]
in:  [16000, 70, 10, 15, 136, 1509, 206, 208, 59, 148, 71, 8, 47, 89, 3, 4, 10, 221, 91, 66, 3, 4, 69, 342, 14, 273, 440, 97, 5, 168, 63, 8, 120, 1091, 43, 151, 910, 206, 215, 4, 27, 3, 16001]
out:  [259, 3, 2517]
in:  [16000, 9186, 64, 8, 610, 11223, 3, 4, 4017, 21, 16, 564, 5464, 11, 2167, 8463, 140, 190, 36, 318, 5, 11223, 547, 3, 1481, 4, 10588, 144, 564, 135, 28, 21, 274, 4017, 11, 186, 339, 3, 2090, 648, 34, 16001]
out:  [186, 3, 2517]
in:  [16000, 266, 289, 9, 30, 16001]
out:  [3210, 3, 2517]
in:  [1600

100%|██████████████████████████████████████| 2000/2000 [00:04<00:00, 429.51it/s]

in:  [16000, 1110, 117, 4, 72, 10, 29, 41, 21, 7, 22, 319, 1071, 16001]
out:  [3210, 3, 2517]
in:  [16000, 4, 27, 295, 282, 17, 5, 44, 16, 225, 240, 3, 45, 19, 18, 365, 150, 9, 367, 44, 3, 16001]
out:  [303, 3, 2517]
in:  [16000, 4, 68, 5, 50, 23, 2348, 25, 4, 201, 138, 8, 199, 30, 11, 5, 371, 26, 16001]
out:  [259, 3, 2517]
in:  [16000, 83, 44, 16001]
out:  [303, 3, 2517]
in:  [16000, 751, 13, 87, 3, 236, 42, 138, 231, 5, 50, 1138, 480, 85, 11635, 22, 58, 162, 26, 3, 4, 223, 112, 99, 114, 360, 240, 178, 3, 358, 555, 1933, 202, 98, 572, 9, 5821, 3, 39, 531, 1450, 8153, 7, 69, 4601, 28, 2029, 3, 96, 19, 8, 439, 26, 6, 36, 1118, 3, 16001]
out:  [303, 3, 2517]
in:  [16000, 139, 819, 9, 5, 62, 18, 559, 605, 65, 114, 360, 101, 446, 6, 23, 491, 634, 3, 4, 763, 5, 2868, 245, 177, 5, 98, 625, 6, 249, 4, 41, 14, 28, 18, 135, 549, 6, 7, 24, 19, 11087, 11, 515, 571, 3, 39, 12, 10897, 84, 30, 245, 275, 169, 55, 8, 120, 184, 6, 23, 5, 156, 30, 1430, 1226, 9, 46, 13001, 6, 7, 69, 376, 1863, 5608, 17

In [ ]:
class GPTBlock(nn.Module):
    def __init__(self, emb_dim, num_heads, ff_dim, dropout=0.1):
        super().__init__()

        self.ln1 = nn.LayerNorm(emb_dim)
        self.attn = nn.MultiheadAttention(
            emb_dim, num_heads, dropout=dropout, batch_first=True
        )

        self.ln2 = nn.LayerNorm(emb_dim)
        self.ff = nn.Sequential(
            nn.Linear(emb_dim, ff_dim),
            nn.ReLU(),
            nn.Linear(ff_dim, emb_dim),
        )
        self.dropout = nn.Dropout(dropout)

    def forward(self, x, attn_mask=None, key_padding_mask=None):
        # self-attention only
        h = self.ln1(x)
        h, _ = self.attn(
            h, h, h,
            attn_mask=attn_mask,
            key_padding_mask=key_padding_mask
        )
        x = x + self.dropout(h)

        # feedforward
        h2 = self.ln2(x)
        h2 = self.ff(h2)
        x = x + self.dropout(h2)

        return x

class DecoderOnlyTransformer(nn.Module):
    def __init__(self, vocab_size, emb_dim=1024, num_heads=8,
                 num_layers=12, ff_dim=512, max_len=800, dropout=0.5):
        super().__init__()

        self.embedding = nn.Embedding(vocab_size, emb_dim, padding_idx=0)
        self.pos_embed = nn.Embedding(max_len, emb_dim)

        self.blocks = nn.ModuleList([
            GPTBlock(emb_dim, num_heads, ff_dim, dropout)
            for _ in range(num_layers)
        ])

        self.ln_f = nn.LayerNorm(emb_dim)
        self.fc = nn.Linear(emb_dim, 5)

    def forward(self, x, lengths):
        B, L = x.shape

        pos = torch.arange(L, device=x.device).unsqueeze(0)
        h = self.embedding(x) + self.pos_embed(pos)

        causal_mask = torch.triu(
            torch.ones(L, L, device=x.device), diagonal=1
        ).bool()

        pad_mask = (x == 0)

        for block in self.blocks:
            h = block(h, attn_mask=causal_mask, key_padding_mask=pad_mask)

        h = self.ln_f(h)

        idx = (lengths - 1).view(-1, 1, 1).expand(-1, 1, h.size(-1))
        last_hidden = h.gather(1, idx).squeeze(1)

        return self.fc(last_hidden)


def collate_fn(batch):
    sequences, labels = zip(*batch)

    lengths = torch.tensor([len(seq) for seq in sequences])

    padded = pad_sequence(
        sequences,
        batch_first=True, 
        padding_value=0
    )

    labels = torch.stack([l for l in labels])
    return padded, lengths, labels


class ReviewDataset(Dataset):
    def __init__(self, train_dframe, spm_model):
        self.df = train_dframe
        self.sp = spm.SentencePieceProcessor()
        self.sp.load(spm_model)

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        text = self.df.loc[idx, "reviewText"]
        label = torch.tensor(self.df.loc[idx, "overall"], dtype = torch.long)
        ids = self.sp.encode(text, out_type=int)
        ids_encoded = [start_token] + ids + [end_token]
        ids_encoded = torch.tensor(ids_encoded, dtype=torch.long)
        return ids_encoded, label


class ICLDataset(Dataset):
    def __init__(self, shot_dict, y, shots):
        self.ICL_shot = shot_dict[shots]
        self.y = y

    def __len__(self):
        return len(self.ICL_shot)

    def __getitem__(self, idx):
        text = self.ICL_shot[idx]
        label = torch.tensor(self.y[idx], dtype=torch.long)
        
        #label = self.df.loc[idx, "overall"].item()
        #one_hot_encoded_label = F.one_hot(label, num_classes=5).squeeze(0)
        #ids = self.sp.encode(text, out_type=int)
        ids = torch.tensor(text, dtype=torch.long)

        return ids, label

shot_ex = 10
icl_dataset = ICLDataset(annos_x, annos_y, shot_ex)
icl_loader = DataLoader(
    icl_dataset,
    batch_size=50,
    shuffle=True,
    collate_fn=collate_fn
)



train_dataset = ReviewDataset(train_df, "amazon_reviews.model")
train_loader = DataLoader(
    train_dataset,
    batch_size=50,
    shuffle=True,
    collate_fn=collate_fn
)

test_dataset = ReviewDataset(test_df, "amazon_reviews.model")
test_loader = DataLoader(
    test_dataset,
    batch_size=50,
    shuffle=True,
    collate_fn=collate_fn
)

max_len = 0
for padded, lengths, labels in icl_loader:
    batch_max = lengths.max().item()
    max_len = max(max_len, batch_max)
    
for padded, lengths, labels in train_loader:
    batch_max = lengths.max().item()
    max_len = max(max_len, batch_max)



for padded, lengths, labels in test_loader:
    batch_max = lengths.max().item()
    max_len = max(max_len, batch_max)


print("max_len", max_len)




In [ ]:
# Loading Data

model = DecoderOnlyTransformer(vocab_size+2, max_len = max_len)
model = model.to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=1e-4)
criterion = nn.CrossEntropyLoss()
epochs = 15

total_params = sum(p.numel() for p in model.parameters() if p.requires_grad)
print(f"Trainable parameters: {total_params}")


def train(model, dataloader, optimizer, criterion, epochs):
    model.train()
    track_loss = []
    total_loss = 0
    for i in range(epochs):
        model.train()
        total_loss = 0
        
        train_data_loader = tqdm(dataloader)
        
        for padded, lengths, labels in train_data_loader:
            padded = padded.to(device)
            lengths = lengths.to(device)
            labels = labels.to(device)
    
            optimizer.zero_grad()
            outputs = model(padded, lengths)


            loss = criterion(outputs, labels)
            track_loss.append(loss.item())
            avg = sum(track_loss[-10:])/10
    
            loss.backward()
            optimizer.step()
    
            total_loss += loss.item()
            train_data_loader.set_postfix(loss=avg)
            del outputs, loss
            torch.cuda.empty_cache()
        model.eval()
        total_val_loss = 0
        corr =0
        ll = 0

        with torch.no_grad():
            for padded, lengths, labels in test_loader:
                padded = padded.to(device)
                lengths = lengths.to(device)
                labels = labels.to(device)
                outputs = model(padded, lengths)


                loss = criterion(outputs, labels)

                v = torch.argmax(outputs, dim =1)
                delt = torch.sum(v==labels)
                ll+= len(v)
                corr += delt

                total_val_loss += loss.item()

        print("Epoch", i+1, "track loss: ", total_loss / len(train_data_loader), " val loss: ", total_val_loss / len(test_loader), "val acc: ", corr / len_test )
    return total_loss, track_loss

In [27]:
loss, tracked_loss = train(model, train_loader, optimizer, criterion, epochs)


100%|███████████████████████████████| 308/308 [00:32<00:00,  9.44it/s, loss=1.4]


Epoch 1 track loss:  1.4813482227263512  val loss:  1.3415442612264064 val acc:  tensor(0.4102, device='cuda:0')


100%|██████████████████████████████| 308/308 [00:32<00:00,  9.43it/s, loss=1.29]


Epoch 2 track loss:  1.2899153698961456  val loss:  1.1755781227892095 val acc:  tensor(0.4879, device='cuda:0')


100%|██████████████████████████████| 308/308 [00:32<00:00,  9.56it/s, loss=1.24]


...

Epoch 13 track loss:  0.47456367400946553  val loss:  0.5642753854974524 val acc:  tensor(0.8452, device='cuda:0')


100%|█████████████████████████████| 308/308 [00:33<00:00,  9.31it/s, loss=0.545]


Epoch 14 track loss:  0.44322648267080256  val loss:  0.5428722953641569 val acc:  tensor(0.8478, device='cuda:0')


100%|█████████████████████████████| 308/308 [00:32<00:00,  9.35it/s, loss=0.497]


Epoch 15 track loss:  0.39783660820745803  val loss:  0.5318011021265736 val acc:  tensor(0.8605, device='cuda:0')


In [36]:
annos_x[1]

[[16000,
  4,
  72,
  10,
  29,
  41,
  24,
  44,
  3,
  45,
  19,
  167,
  53,
  767,
  3,
  4,
  605,
  21,
  547,
  3,
  45,
  19,
  82,
  44,
  23,
  22,
  111,
  10,
  29,
  26,
  3,
  16001,
  3210,
  3,
  2517,
  16000,
  751,
  352,
  121,
  199,
  745,
  9,
  98,
  572,
  17,
  5,
  161,
  30,
  3,
  3325,
  614,
  8,
  125,
  30,
  331,
  9,
  290,
  92,
  25,
  13,
  43,
  3,
  1885,
  7,
  704,
  301,
  217,
  3,
  6702,
  22,
  58,
  334,
  57,
  51,
  7,
  46,
  1262,
  172,
  3,
  16001],
 [16000,
  1507,
  7,
  40,
  49,
  134,
  43,
  351,
  28,
  1158,
  34,
  4,
  2943,
  41,
  5,
  161,
  30,
  116,
  1195,
  92,
  5,
  75,
  6,
  37,
  911,
  7,
  8,
  74,
  429,
  25,
  5,
  467,
  28,
  297,
  19,
  8,
  74,
  184,
  7,
  631,
  26,
  13,
  66,
  327,
  3,
  39,
  143,
  671,
  462,
  402,
  1075,
  7,
  146,
  38,
  134,
  116,
  1580,
  3,
  16001,
  186,
  3,
  2517,
  16000,
  45,
  19,
  375,
  49,
  7,
  1348,
  1029,
  2126,
  22,
  86,
  38,
  28,
  65,
 

In [28]:
torch.cuda.empty_cache()

In [29]:
model.eval()
total_val_loss = 0
corr =0
ll = 0

In [30]:
model.eval()

def predict(text):
    ids = torch.tensor(tok.encode(text, out_type=int)).unsqueeze(0)
    lengths = torch.tensor([len(ids)])
    ids = ids.to(device)
    lengths = lengths.to(device)
    with torch.no_grad():
        out = model(ids, lengths)
        ao = torch.argmax(out)
    return ao

#print("Prediction for <I love this book>", predict("I love this book"))

model.eval()
total_val_loss = 0
corr =0

with torch.no_grad():
    for padded, lengths, labels in test_loader:
        padded = padded.to(device)
        lengths = lengths.to(device)
        labels = labels.to(device)
        outputs = model(padded, lengths)


        loss = criterion(outputs, labels)

        v = torch.argmax(outputs, dim =1)
        delt = torch.sum(v==labels)
        corr += delt

        total_val_loss += loss.item()
        del outputs, loss
        torch.cuda.empty_cache()

print("val acc: ", corr / len_test )

val acc:  tensor(0.8605, device='cuda:0')


In [31]:

total_train_loss = 0
corr =0

with torch.no_grad():
    for padded, lengths, labels in train_loader:
        padded = padded.to(device)
        lengths = lengths.to(device)
        labels = labels.to(device)
        outputs = model(padded, lengths)


        loss = criterion(outputs, labels)

        v = torch.argmax(outputs, dim =1)
        delt = torch.sum(v==labels)
        corr += delt

        total_train_loss += loss.item()
        del outputs, loss
        torch.cuda.empty_cache()

print("train acc: ", corr / len_train)


train acc:  tensor(0.9472, device='cuda:0')


In [32]:
class ICLDataset(Dataset):
    def __init__(self, shot_dict, y, shots):
        self.ICL_shot = shot_dict[shots]
        self.y = y

    def __len__(self):
        return len(self.ICL_shot)

    def __getitem__(self, idx):
        text = self.ICL_shot[idx]
        label = torch.tensor(self.y[idx], dtype=torch.long)
        
        #label = self.df.loc[idx, "overall"].item()
        #one_hot_encoded_label = F.one_hot(label, num_classes=5).squeeze(0)
        #ids = self.sp.encode(text, out_type=int)
        ids = torch.tensor(text, dtype=torch.long)

        return ids, label



In [33]:
n

[0, 1, 2, 3, 5, 7, 10]

In [35]:
for shot_ex in n:
    icl_dataset = ICLDataset(annos_x, annos_y, shot_ex)
    icl_loader = DataLoader(
        icl_dataset,
        batch_size=50,
        shuffle=True,
        collate_fn=collate_fn
    )
    
    max_len = 0
    for padded, lengths, labels in icl_loader:
        batch_max = lengths.max().item()
        max_len = max(max_len, batch_max)
    
    print("max_len", max_len)
    
    """
    ll = 0
    corr = 0
    total_icl_loss = 0
    with torch.no_grad():
        for padded, lengths, labels in icl_loader:
            lengths = lengths.to(device)
            labels =  labels.to(device)
            padded = padded.to(device)
    
            outputs = model(padded, lengths)
            v = torch.argmax(outputs, dim = 1)
            corr += sum(v==labels)
            ll += len(v)
            loss = criterion(outputs, labels)
            total_icl_loss += loss.item()
    
    torch.cuda.empty_cache()
    avg_icl = total_icl_loss / len(icl_loader)
    icl_acc = corr / ll
    print(shot_ex, avg_icl, icl_acc)
    """

max_len 82
max_len 158
max_len 221
max_len 263
max_len 407
max_len 445
max_len 588


In [ ]:
max_len = 0
for padded, lengths, labels in icl_loader:
    batch_max = lengths.max().item()
    max_len = max(max_len, batch_max)

print("max_len", max_len)


In [10]:
class ICLDataset(Dataset):
    def __init__(self, shot_dict, y, shots):
        self.ICL_shot = shot_dict[shots]
        self.y = y

    def __len__(self):
        return len(self.ICL_shot)

    def __getitem__(self, idx):
        text = self.ICL_shot[idx]
        label = torch.tensor(self.y[idx], dtype=torch.long)
        
        #label = self.df.loc[idx, "overall"].item()
        #one_hot_encoded_label = F.one_hot(label, num_classes=5).squeeze(0)
        #ids = self.sp.encode(text, out_type=int)
        ids = torch.tensor(text, dtype=torch.long)

        return ids, label



In [11]:
n

[0, 1, 2, 3, 5, 7, 10]